In [16]:
import sqlite3

import pandas as pd

from sklearn.feature_extraction.text import CountVectorizer

# CONFIG
DB_PATH = '1_after_cleaning_databases/1000_calc_media.db'
TABLE_NAME = 'css_attribute'
OUTPUT_NAME = 'feature_matrix_media_calc'

## PANDAS
pd.set_option('future.no_silent_downcasting', True)
# Set pandas options to display the full DataFrame
pd.set_option('display.max_rows', None)  # Show all rows
pd.set_option('display.max_columns', None)  # Show all columns
pd.set_option('display.width', None)  # Disable line wrapping
pd.set_option('display.max_colwidth', None)  # Show full content in each column
pd.set_option('display.max_seq_item', 100000)  # Show all items in a sequence (e.g., lists, dictionaries)

# Optionally, increase the display buffer size
pd.set_option('display.max_info_columns', 100000)  # Show all columns in df.info()

# If you have very large dataframes, increasing this might help
pd.set_option('display.max_rows', 1000)  # You can change 1000 to a higher value if needed

### Functions

#### Loading data from sqlite to pandas dataframe

In [17]:
def load_sqlite_to_dataframe(db_path, table_name):
    conn = sqlite3.connect(db_path)
    df = pd.read_sql(f"SELECT * FROM {table_name}", conn)
    conn.close()
    return df

#### Changing boolean values to 1 and 0

In [18]:
def convert_booleans(value):
    true_values = {'enabled'}
    false_values = {'disabled'}

    if isinstance(value, str):
        val_lower = value.lower()
        if val_lower in true_values:
            return 1
        elif val_lower in false_values:
            return 0
    return value

#### Constructing feature matrix

In [19]:
def create_feature_matrix(df):
    # Handle fonts
    fonts = (
        df[df['attribute'] == 'font']
        .groupby('session_id')['value']
        .apply(lambda x: ';'.join(sorted(set(x))))
        .reset_index()
    )

    # replace spaces in font names with underscores
    fonts['value'] = fonts['value'].str.replace(' ', '_', regex=False)

    # Rest of features
    non_fonts = df[df['attribute'] != 'font'].copy()
    non_fonts['feature_name'] = non_fonts['source'] + ':' + non_fonts['attribute']

    # Apply boolean conversion
    non_fonts['value'] = non_fonts['value'].apply(convert_booleans)

    # Pivot table
    pivot = non_fonts.pivot_table(index='session_id',
                                  columns='feature_name',
                                  values='value',
                                  aggfunc='first').reset_index()

    # Merge fonts back
    full_df = pivot.merge(fonts, on='session_id', how='left')

    full_df.rename(columns={'value': 'fonts'}, inplace=True)

    return full_df

#### Changing font values to one-hot encoding

In [20]:
def vectorize_fonts(df, font_column='fonts'):
    vectorizer = CountVectorizer(tokenizer=lambda x: [token.strip() for token in x.split(';') if token.strip()])
    font_features = vectorizer.fit_transform(df[font_column].fillna(''))

    font_df = pd.DataFrame(
        font_features.toarray(),
        columns=[f'css:font_{f}' for f in vectorizer.get_feature_names_out()],
        index=df.index
    )

    font_df['css:font_vector'] = font_df.astype(str).agg(''.join, axis=1)

    df = df.drop(columns=[font_column]).join(font_df)
    return df

#### Cleaning feature types

In [21]:
def clean_feature_types(df):
    for col in df.columns:
        # todo bedzie trzeba na to spojrzec gdy dojda kolejne atrybuty bo jest to takie niezbyt uniwersalne
        if col.startswith('css:env') or col.startswith("css:media") or col.startswith('js:env') or 'width' in col or 'height' in col:
            df[col] = pd.to_numeric(df[col], errors='coerce')

    # Fill missing numeric with -1
    numeric_cols = df.select_dtypes(include='number').columns
    df[numeric_cols] = df[numeric_cols].fillna(-1)

    # Fill missing non-numeric with empty string
    object_cols = df.select_dtypes(include='object').columns
    df[object_cols] = df[object_cols].fillna('')

    df = df.infer_objects()

    return df

#### Save datagframe to parquet

In [22]:
def save_features(df):
    df.to_parquet(f'2_after_feature_extraction/{OUTPUT_NAME}.parquet')
    df.to_csv(f'2_after_feature_extraction/{OUTPUT_NAME}.csv', index=False)

### Execution

In [23]:
# Load data
df_raw = load_sqlite_to_dataframe(DB_PATH, TABLE_NAME)

In [24]:
# Create feature matrix
df_features = create_feature_matrix(df_raw)

In [25]:
df_features

session_id browserstack:browser  \
0    0049b167-77a4-4a03-9b6b-bf83485e0fae               chrome   
1    005ffba4-b5d6-42d6-bea1-d678a7986805                 edge   
2    00753e05-2b50-47cf-a387-2aebb1e0645c                 edge   
3    007a487e-fe9b-4519-867f-bd043b7d3cc9              firefox   
4    00977aea-b024-4b43-8f10-89b9323fe77a       chrome_android   
5    00e5efaf-23b5-4884-9b6a-7bb5df20ffcc              firefox   
6    010c339b-09a6-43f5-aa80-bd9d71564bb2               chrome   
7    019427d2-f7c6-4796-97a3-60a4f3058c1e              firefox   
8    021e4bf3-a0b7-4ce9-8a52-5cf56594feb2       chrome_android   
9    02bf78dc-6ebd-4cf5-b7f0-91ae2d131e6e               chrome   
10   0318178e-ba41-4c28-8352-2386da82b23c               chrome   
11   0322b869-b54d-41fe-97e9-cfb3b098a9ee              firefox   
12   033b0569-3ed2-46a8-b73d-a1aa481a0df9              firefox   
13   039db514-8178-4c1d-9f90-fa21144b2952               chrome   
14   03bed3d4-8f56-4f64-bab5-b8f9be688d69                 edge   
15   0416adf2-b3bb-4237-8e0a-ec7da3b63d3f                 edge   
16   04201632-1ada-4c9b-ba81-dcebede476df               chrome   
17   04a3b044-484e-4674-85c2-001ef4c9e529              firefox   
18   04ad29e2-e406-4282-8137-0027350564ed      chromium_iphone   
19   056a94dc-9589-40ba-bbb8-1c1ff04ebe17              firefox   
20   05b0c855-1aab-4403-82e0-5968c3aca9e9               chrome   
21   05f0d7f4-8659-4c95-baaf-dc58c632b887                 edge   
22   0619984c-cf24-4a63-b7b6-a1e2bf2ad52d               chrome   
23   06bff118-c8f9-495f-82dd-085b8eb8943f              firefox   
24   072bf174-33b9-45ad-a7f6-7c8866b8fb75               chrome   
25   075ce538-b8f9-4444-96f8-306a2c7b114b              firefox   
26   075f3f8a-8edb-4907-9538-884b87f2aca0                 edge   
27   076d4e0b-caef-4f76-aaab-d5ecbb115806        chromium_ipad   
28   07884c68-9103-45a7-8876-a649210b7c19                 edge   
29   078b58e0-51fb-4210-8293-a7046b5d95bf               chrome   
30   078e085a-fb0b-44a7-a14a-70df27e9c517              firefox   
31   07c5575c-365c-463d-b1b3-baf3d3b49826                 edge   
32   0865e8c6-4040-4433-b6dd-4ed522e862b3       chrome_android   
33   08a6e9b8-c5c6-4387-bb9d-fbf7984b4522              firefox   
34   08dc9aca-b1a5-4371-a175-8c1e1ae7e61e                 edge   
35   096a5a79-e75a-4adc-9c2e-73555d11b686               chrome   
36   098a6a9e-b815-4894-a838-07afb99c95b8               chrome   
37   098e989c-c47d-45f9-bd4c-50093b5aa5d7                 edge   
38   0a6e4cc2-4d8b-4725-a647-6048c050a4c4               chrome   
39   0a827209-b4a2-400e-b322-28a56d11d8bf              firefox   
40   0a95ff34-23b6-44f0-b1ee-f4bd72385476               chrome   
41   0ad37b93-cc03-4f8c-bb24-4ba1b69b20e7       chrome_android   
42   0ae4053d-63ea-4cfa-8da9-34ea1b901ff7               chrome   
43   0af78a55-fe53-4b73-aa49-2441c6a46649               chrome   
44   0baf5ce7-0bc5-4da5-bf17-0695fec4e432              firefox   
45   0bdbf07c-9af7-48c5-8930-67d3e8692a01               chrome   
46   0c178cad-7c32-4d34-a44a-d661401e27fa               chrome   
47   0c6cc684-3e12-4b23-ac38-4c50fd6c3f7e               chrome   
48   0c9121b1-7711-4d05-ae93-aa4fe787a91a               chrome   
49   0ca395df-029e-43fd-9c3e-b8d26c485204                 edge   
50   0cb03fd0-71b7-4df4-99aa-a24c5a6c666d                 edge   
51   0cc9d024-2833-43ad-911e-946ea828e46c              firefox   
52   0d3ffbcd-0bfa-4bdd-a374-edc49a673fda                 edge   
53   0d57e7d5-aafe-4f7c-b4ad-d32904a838d5              firefox   
54   0d5823ff-1eaa-433c-a129-0a0ac1755b4c              samsung   
55   0d7facd9-1678-4770-999e-2df64bd7342e              firefox   
56   0d8ab648-3f2c-4834-a5f5-d3cb68b61a01                 edge   
57   0d8b4180-be65-4b74-b5b6-832c901e9c31                 edge   
58   0d8f522f-5626-451a-a8b9-eddba7356bce              firefox   
59   0deb975f-1bed-47c4-b769-a0655b92242c                 edge   
60   

In [26]:
# Vectorize fonts
df_features = vectorize_fonts(df_features)

C:\Programs\TBO\tbo-task1\Python\Flask_Book_Library\.venv\Lib\site-packages\sklearn\feature_extraction\text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


In [27]:
# Clean feature types
df_ready = clean_feature_types(df_features)

In [28]:
# test Output
print(f"Shape of feature matrix: {df_ready.shape}")
display(df_ready.head())

Shape of feature matrix: (922, 142)


session_id browserstack:browser  \
0  0049b167-77a4-4a03-9b6b-bf83485e0fae               chrome   
1  005ffba4-b5d6-42d6-bea1-d678a7986805                 edge   
2  00753e05-2b50-47cf-a387-2aebb1e0645c                 edge   
3  007a487e-fe9b-4519-867f-bd043b7d3cc9              firefox   
4  00977aea-b024-4b43-8f10-89b9323fe77a       chrome_android   

  browserstack:browser_version browserstack:os browserstack:os_version  \
0                        114.0            OS X                  Mojave   
1                        118.0            OS X                  Sonoma   
2                        113.0            OS X                 Sequoia   
3                        112.0         Windows                       7   
4                      unknown         android                    10.0   

   browserstack:real_height  browserstack:real_width  \
0                      1013                     1200   
1                      1011                     1200   
2                      1011                     1200   
3                       980                     1296   
4                       727                      393   

                                                                                                                            css:User-Agent  \
0                    Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/114.0.0.0 Safari/537.36   
1  Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/118.0.0.0 Safari/537.36 Edg/118.0.2088.46   
2  Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/113.0.0.0 Safari/537.36 Edg/113.0.1774.35   
3                                                          Mozilla/5.0 (Windows NT 6.1; Win64; x64; rv:109.0) Gecko/20100101 Firefox/112.0   
4                          Mozilla/5.0 (Linux; Android 10; K) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/128.0.0.0 Mobile Safari/537.36   

   css:calc-10-width  css:calc-2-width  css:calc-3-width  css:calc-4-width  \
0           0.239583          7.937500        279.102000          6.496094   
1           0.239583          7.937500        279.102000          6.496094   
2           0.239583          7.937500        279.102000          6.496094   
3          50.033300          0.000000         94.483300          3.183330   
4           5.602941          7.953125        274.921875          6.496094   

   css:calc-5-width  css:calc-6-width  css:calc-7-width  css:calc-8-width  \
0          0.604167        938.685000         19.601600        139.102000   
1          0.604167        938.685000         19.601600        139.102000   
2          0.604167        938.685000         19.601600        139.102000   
3          0.000000       2107.983398         16.500000          0.000000   
4          0.370536        938.622253         19.651787         59.558338   

   css:calc-9-width  css:env-1-height  css:env-1-width  css:env-10-height  \
0          0.207031               136              195                166   
1          0.207031               136              195                166   
2          0.207031               136              195                166   
3          0.000000               136              189                311   
4          0.327381               130              224                169   

   css:env-10-width  css:env-11-height  css:env-11-width  css:env-12-height  \
0               711                175              1100                123   
1               712                175              1100                123   
2               711                175              1100                124   
3               421                166              1100                127   
4               785                167              1100                121   

   css:env-12-width  css:env-13-height  css:env-13-width  css:env-14-height  \
0              6763                125                84    

In [29]:
# how many features there are with css in its name
df_ready.filter(regex='css').shape[1]

67

In [30]:
save_features(df_ready)

In [31]:
# list all columns
print(df_ready.columns)

Index(['session_id', 'browserstack:browser', 'browserstack:browser_version',
       'browserstack:os', 'browserstack:os_version',
       'browserstack:real_height', 'browserstack:real_width', 'css:User-Agent',
       'css:calc-10-width', 'css:calc-2-width', 'css:calc-3-width',
       'css:calc-4-width', 'css:calc-5-width', 'css:calc-6-width',
       'css:calc-7-width', 'css:calc-8-width', 'css:calc-9-width',
       'css:env-1-height', 'css:env-1-width', 'css:env-10-height',
       'css:env-10-width', 'css:env-11-height', 'css:env-11-width',
       'css:env-12-height', 'css:env-12-width', 'css:env-13-height',
       'css:env-13-width', 'css:env-14-height', 'css:env-14-width',
       'css:env-2-height', 'css:env-2-width', 'css:env-3-height',
       'css:env-3-width', 'css:env-5-height', 'css:env-5-width',
       'css:env-6-height', 'css:env-6-width', 'css:env-7-height',
       'css:env-7-width', 'css:env-8-height', 'css:env-8-width',
       'css:env-9-height', 'css:env-9-width', 'css:ima